In [ ]:
from google.colab import drive
drive.mount('/content/drive')

In [ ]:
!apt -y install -qq aria2
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/camenduru/joy-caption-alpha-one/raw/main/text_model/adapter_config.json -d /content/joy/text_model -o adapter_config.json
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/camenduru/joy-caption-alpha-one/resolve/main/text_model/adapter_model.safetensors -d /content/joy/text_model -o adapter_model.safetensors
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/camenduru/joy-caption-alpha-one/resolve/main/clip_model.pt -d /content/joy -o clip_model.pt
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/camenduru/joy-caption-alpha-one/raw/main/config.yaml -d /content/joy -o config.yaml
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/camenduru/joy-caption-alpha-one/resolve/main/image_adapter.pt -d /content/joy -o image_adapter.pt

!apt -y install -qq aria2
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/camenduru/joy-caption-alpha-one/raw/main/text_model/adapter_config.json -d /content/joy/text_model -o adapter_config.json
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/camenduru/joy-caption-alpha-one/resolve/main/text_model/adapter_model.safetensors -d /content/joy/text_model -o adapter_model.safetensors
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/camenduru/joy-caption-alpha-one/resolve/main/clip_model.pt -d /content/joy -o clip_model.pt
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/camenduru/joy-caption-alpha-one/raw/main/config.yaml -d /content/joy -o config.yaml
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/camenduru/joy-caption-alpha-one/resolve/main/image_adapter.pt -d /content/joy -o image_adapter.pt

#  Use a custom prompt to instruct the image captioning model
custom_prompt = '' #{type:'string'}
enable_custom_prompt = False #  {type:'boolean'}
if not enable_custom_prompt: custom_prompt = 'Describe the image in 400 words'
!pip install peft bitsandbytes
!pip install hf_xet
from huggingface_hub import InferenceClient
from torch import nn
from transformers import AutoModel, BitsAndBytesConfig, AutoProcessor, AutoTokenizer, PreTrainedTokenizer, PreTrainedTokenizerFast, AutoModelForCausalLM
import torch
import torch.amp
from PIL import Image
import os
import torchvision.transforms.functional as TVF

CLIP_PATH = "google/siglip-so400m-patch14-384"
MODEL_PATH = "unsloth/Meta-Llama-3.1-8B-bnb-4bit"
CAPTION_TYPE_MAP = {
    ("descriptive", "formal", False, False): [f"{custom_prompt}"],
}

class ImageAdapter(nn.Module):
	def __init__(self, input_features: int, output_features: int, ln1: bool, pos_emb: bool, num_image_tokens: int, deep_extract: bool):
		super().__init__()
		self.deep_extract = deep_extract
		if self.deep_extract:
			input_features = input_features * 5
		self.linear1 = nn.Linear(input_features, output_features)
		self.activation = nn.GELU()
		self.linear2 = nn.Linear(output_features, output_features)
		self.ln1 = nn.Identity() if not ln1 else nn.LayerNorm(input_features)
		self.pos_emb = None if not pos_emb else nn.Parameter(torch.zeros(num_image_tokens, input_features))
		self.other_tokens = nn.Embedding(3, output_features)
		self.other_tokens.weight.data.normal_(mean=0.0, std=0.02)   # Matches HF's implementation of llama3
	def forward(self, vision_outputs: torch.Tensor):
		if self.deep_extract:
			x = torch.concat((
				vision_outputs[-2],
				vision_outputs[3],
				vision_outputs[7],
				vision_outputs[13],
				vision_outputs[20],
			), dim=-1)
			assert len(x.shape) == 3, f"Expected 3, got {len(x.shape)}"  # batch, tokens, features
			assert x.shape[-1] == vision_outputs[-2].shape[-1] * 5, f"Expected {vision_outputs[-2].shape[-1] * 5}, got {x.shape[-1]}"
		else:
			x = vision_outputs[-2]
		x = self.ln1(x)
		if self.pos_emb is not None:
			assert x.shape[-2:] == self.pos_emb.shape, f"Expected {self.pos_emb.shape}, got {x.shape[-2:]}"
			x = x + self.pos_emb
		x = self.linear1(x)
		x = self.activation(x)
		x = self.linear2(x)
		other_tokens = self.other_tokens(torch.tensor([0, 1], device=self.other_tokens.weight.device).expand(x.shape[0], -1))
		assert other_tokens.shape == (x.shape[0], 2, x.shape[2]), f"Expected {(x.shape[0], 2, x.shape[2])}, got {other_tokens.shape}"
		x = torch.cat((other_tokens[:, 0:1], x, other_tokens[:, 1:2]), dim=1)
		return x
	def get_eot_embedding(self):
		return self.other_tokens(torch.tensor([2], device=self.other_tokens.weight.device)).squeeze(0)

clip_processor = AutoProcessor.from_pretrained(CLIP_PATH)
clip_model = AutoModel.from_pretrained(CLIP_PATH)
clip_model = clip_model.vision_model
checkpoint = torch.load("/content/joy/clip_model.pt", map_location='cpu')
checkpoint = {k.replace("_orig_mod.module.", ""): v for k, v in checkpoint.items()}
clip_model.load_state_dict(checkpoint)
# del checkpoint
clip_model.eval()
clip_model.requires_grad_(False)
clip_model.to("cuda")
tokenizer = AutoTokenizer.from_pretrained(f'{MODEL_PATH}')
#tokenizer = AutoTokenizer.from_pretrained("unsloth/Meta-Llama-3.1-8B-bnb-4bit")
assert isinstance(tokenizer, PreTrainedTokenizer) or isinstance(tokenizer, PreTrainedTokenizerFast), f"Tokenizer is of type {type(tokenizer)}"
text_model = AutoModelForCausalLM.from_pretrained(MODEL_PATH, quantization_config = BitsAndBytesConfig(load_in_8bit=True), device_map="auto", torch_dtype=torch.bfloat16)
text_model.load_adapter("/content/joy/text_model")
text_model.eval()
image_adapter = ImageAdapter(clip_model.config.hidden_size, text_model.config.hidden_size, False, False, 38, False)
image_adapter.load_state_dict(torch.load("/content/joy/image_adapter.pt", map_location="cpu"))
image_adapter.eval()
image_adapter.to("cuda")

In [2]:
# @markdown higher temperature = prompt creativity (default 0.6) <br> higher top_p = higher noise reduction in latent embedding (default 0.9)
temperature = 1.2 # @param {type:'slider',min:0.5,max:4.0,step:0.05}
top_p = 0.85 # @param {type:'slider',min:0.1,max:0.95,step:0.05}
temperature = float(temperature)
top_p = float(top_p)
#-----#
num=1
#import torch
#import Image

@torch.no_grad()
def stream_chat(input_image: Image.Image, prompt_str: str) -> str:
    torch.cuda.empty_cache()
    length =512
    #length = None if caption_length == "any" else caption_length
    #if isinstance(length, str):
    #    try:
    #       length = int(length)
    #    except ValueError:
    #        pass
    #if caption_type == "rng-tags" or caption_type == "training_prompt":
    #    caption_tone = "formal"
    #prompt_key = (caption_type, caption_tone, isinstance(length, str), isinstance(length, int))
    #if prompt_key not in CAPTION_TYPE_MAP:
    #    raise ValueError(f"Invalid caption type: {prompt_key}")
    #prompt_str = CAPTION_TYPE_MAP[prompt_key][0].format(length=length, word_count=length)
    print(f"Prompt: {prompt_str}")
    image = input_image.resize((384, 384), Image.LANCZOS)
    pixel_values = TVF.pil_to_tensor(image).unsqueeze(0) / 255.0
    pixel_values = TVF.normalize(pixel_values, [0.5], [0.5])
    pixel_values = pixel_values.to('cuda')
    prompt = tokenizer.encode(prompt_str, return_tensors='pt', padding=False, truncation=False, add_special_tokens=False)
    with torch.amp.autocast_mode.autocast('cuda', enabled=True):
        vision_outputs = clip_model(pixel_values=pixel_values, output_hidden_states=True)
        image_features = vision_outputs.hidden_states
        embedded_images = image_adapter(image_features)
        embedded_images = embedded_images.to('cuda')
    prompt_embeds = text_model.model.embed_tokens(prompt.to('cuda'))
    assert prompt_embeds.shape == (1, prompt.shape[1], text_model.config.hidden_size), f"Prompt shape is {prompt_embeds.shape}, expected {(1, prompt.shape[1], text_model.config.hidden_size)}"
    embedded_bos = text_model.model.embed_tokens(torch.tensor([[tokenizer.bos_token_id]], device=text_model.device, dtype=torch.int64))
    eot_embed = image_adapter.get_eot_embedding().unsqueeze(0).to(dtype=text_model.dtype)
    inputs_embeds = torch.cat([
        embedded_bos.expand(embedded_images.shape[0], -1, -1),
        embedded_images.to(dtype=embedded_bos.dtype),
        prompt_embeds.expand(embedded_images.shape[0], -1, -1),
        eot_embed.expand(embedded_images.shape[0], -1, -1),
    ], dim=1)
    input_ids = torch.cat([
        torch.tensor([[tokenizer.bos_token_id]], dtype=torch.long),
        torch.zeros((1, embedded_images.shape[1]), dtype=torch.long),
        prompt,
        torch.tensor([[tokenizer.convert_tokens_to_ids("<|eot_id|>")]], dtype=torch.long),
    ], dim=1).to('cuda')
    attention_mask = torch.ones_like(input_ids)
    generate_ids = text_model.generate(input_ids, top_p = top_p , temperature=temperature, inputs_embeds=inputs_embeds, attention_mask=attention_mask, max_new_tokens=3000, do_sample=True, suppress_tokens=None)   # Uses the default which is temp=0.6, top_p=0.9
    generate_ids = generate_ids[:, input_ids.shape[1]:]
    if generate_ids[0][-1] == tokenizer.eos_token_id or generate_ids[0][-1] == tokenizer.convert_tokens_to_ids("<|eot_id|>"):
        generate_ids = generate_ids[:, :-1]
    caption = tokenizer.batch_decode(generate_ids, skip_special_tokens=False, clean_up_tokenization_spaces=False)[0]
    caption = f'{caption.strip()}'.replace('Prompt: Describe the image in 400 words','')
    return caption

In [ ]:

%cd /content/
!unzip training_data.zip









In [ ]:
# @markdown Split the image into 20 parts prior to running
no_parts = 20 # @param {type:'slider', min:1,max:30,step:1}
print(f'Splitting all images found under /content/... \n into {no_parts} along x-axis')
import os,math,random
from PIL import Image
home_directory = '/content/'
using_Kaggle = os.environ.get('KAGGLE_URL_BASE','')
if using_Kaggle : home_directory = '/kaggle/working/'
%cd {home_directory}

def my_mkdirs(folder):
  if os.path.exists(folder)==False:
    os.makedirs(folder)


tgt_folder = f'/content/tmp/'
split_folder = f'/content/split/'
my_mkdirs(f'{split_folder}')


src_folder = '/content/'
suffixes = ['.gif','.png', '.jpeg' , '.webp' , '.jpg']
#num = 1
for filename in os.listdir(src_folder):
  for suffix in suffixes:
    if not filename.find(suffix)>-1: continue
    #while os.path.exists(f'{tgt_folder}{num}.txt'):num = num+1
    print(filename)
    %cd {src_folder}
    textpath = filename.replace(suffix,'.txt')
    #os.remove(f'{filename}')
    #continue
    image = Image.open(f"{filename}").convert('RGB')
    w,h=image.size
    #grid = product(range(0, h-h%d, d), range(0, w-w%d, d))
    divs=no_parts
    step=math.floor(w/divs)
    %cd {split_folder}
    for index in range(divs):
        box = (step*index, 0 ,step*(index+1),math.floor(1.0*h))
        image.crop(box).save(f'{num}_{index}.jpeg','JPEG')
        %cd /content/
        if os.path.exists(textpath):
          with open(f'{textpath}', 'r') as file:
            _tags = file.read()

            print(_tags)
            if not _tags:continue
            tags=''
            _tags = [item.strip() for item in f'{_tags}'.split(',')]
            random.shuffle(_tags)
            for tag in _tags:
              tags = tags + tag + ' , '
            #----#
            tags = (tags + 'AAAA').replace(' , AAAA','')
            prompt_str = f' {tags}'
            %cd {split_folder}
            f = open(f'{num}_{index}.txt','w')
            f.write(f'{prompt_str}')
            f.close()
          #---#
        #-----#
    #----#
    num = num+1
    #caption = stream_chat(input_image, "descriptive", "formal", "any")
    #print(f"...\n\n...caption for {filename}\n\n...")
    #print(caption)
    #---------#
    #f = open(f"{num}.txt", "w")
    #f.write(f'{caption}')
    #f.close()
    #input_image.save(f'{num}.jpeg', "JPEG")
    os.remove(f"{src_folder}{filename}")
    if os.path.exists(f'{src_folder}{textpath}'):os.remove(f'{src_folder}{textpath}')

In [ ]:

import os,random
from PIL import Image
home_directory = '/content/'
using_Kaggle = os.environ.get('KAGGLE_URL_BASE','')
if using_Kaggle : home_directory = '/kaggle/working/'
%cd {home_directory}

def my_mkdirs(folder):
  if os.path.exists(folder)==False:
    os.makedirs(folder)


tgt_folder = f'/content/tmp/'
my_mkdirs(f'{tgt_folder}')
split_folder = '/content/split/'
src_folder = '/content/'
if os.path.exists(f'{split_folder}'): src_folder = f'{split_folder}'
suffixes = ['.gif','.png', '.jpeg' , '.webp' , '.jpg']
num = 1
for filename in os.listdir(src_folder):
  for suffix in suffixes:
    if not filename.find(suffix)>-1: continue
    while os.path.exists(f'{tgt_folder}{num}.txt'):num = num+1
    print(filename)
    %cd {src_folder}
    textpath = filename.replace(suffix,'.txt')
    prompt_str = '< Summary of image > .  < What is the subject? > . < What is the photo? > . < What are the aesthetics? > ' #@param {type:'string'}
    tags =''
    if os.path.exists(f'{src_folder}{textpath}'):
      with open(f'{textpath}', 'r') as file:
        tags = file.read()
        #prompt_str = f'Please improve this prompt : {tags}'
    input_image = Image.open(f"{filename}").convert('RGB')
    caption = stream_chat(input_image, f'{prompt_str} {tags}')
    caption =  caption + tags
    #caption = caption + ", and a logo of a black bar with rainbow glitch art outline that says 'FLUX Chroma V46' psychadelic art"
    print(f"...\n\n...caption for {filename}\n\n...")
    print(caption)
    #---------#
    %cd {tgt_folder}
    f = open(f"{num}.txt", "w")
    f.write(f'{caption}')
    f.close()
    input_image.save(f'{num}.jpeg', "JPEG")
    os.remove(f"{src_folder}{filename}")
    if os.path.exists(f'{src_folder}{textpath}'):os.remove(f'{src_folder}{textpath}')
    num = num+1

In [ ]:
import shutil
%cd /content/
shutil.make_archive('/content/tmp', 'zip', '/content/tmp')

/content


'/content/tmp.zip'

In [ ]:
# @markdown Save images of all urls found in image_urls.txt to workspace

!wget -i image_urls.txt -P ./splits



In [ ]:
# @markdown Auto-disconnect from Google Colab upon running this cell
from google.colab import runtime
#runtime.unassign() #Disconnect from runtime